# Investigating the modification of the DRHODZ variable in the MSIS.f90 subroutine.

DRHODZ is the part of the calculation of the partial derivative of mass density in the D matrix of the variational equations.

This notebook looks at how updating the calculation impacts the DRHODZ term. 


<!-- $$
\frac{d \rho}{d z} = - m_p \bigg( (m_{He}^2 n_{He}) + (m_{O}^2 n_{O}) +  (m_{N2}^2 n_{N2}) + (m_H^2 n_H) + (m_{N}^2 n_{N}) \bigg) \frac{\big(\frac{g_{surf}}{T_{alt} R_{gas}}\big)}{(1 + Z_L / R_E)^2} \bigg(\frac{R_E + Z_L}{R_E + Z_{alt}}\bigg)
$$

Where:
 -  $m_p$ is the mass of a proton  ($=1.66E^{-24}$ grams)
 -  $m_{He}$ is atomic mass of helium ($=4$ amu)
 -  $m_{O}$  is atomic mass of oxygen ($=16$ amu)
 -  $m_{N2}$ is atomic mass of molecular nitrogen ($=28$ amu)
 -  $m_{H}$ is atomic mass of hydrogen ($=1$ amu)
 -  $m_{N}$ is atomic mass of atomic nitrogen ($=14$ amu)
 -  $g_{surf}$ is the gravity at Earth's surface
 -  $T_{alt}$ is the temperature at the given altitude
 -  $R_{gas}$ is the gass constant ($=831.4$)
 -  $Z_{L}$ is the lower boundary for diffusive equilibrium in the MSIS model ($=120$)
  -  $R_E$ is radius of earth 
  -  $Z_{alt}$ is the altitude of the satellite -->

<!-- 
**Below is the code as it appears in the `MSIS.f90` subroutine:**
```fortran
!  Calculate drho/dz.
!
!   IDRV     I    S    =0 MEANS DO NOT FIND DRHODZ, THE CHANGE IN
!                      DENSITY WITH HEIGHT.  =1 MEANS FIND DRHODZ.
      IF(IDRV .NE. 0) THEN
!
! Zach-- added O2 and AR to to species sum
! Zach-- Made the GSURF consistent with ZL
! Zach-- Added separate term for the AnomO scale height
!           to account for the anomolous temperature (4000 K)
!
        GSURF_ZL = GSURF*(RE/(RE + ZL) )**2
!
        TERM1 = ((-1.66D-24*GSURF_ZL)/RGAS)
        TERM_species = (  16.D0*DEN(1)  +  256.D0*DEN(2)                &
     &          + 784.D0*DEN(3)  +    1.D0*DEN(7)                       &
     &          + 196.D0*DEN(8)  + 1024.D0*DEN(4)                       &
     &          + 1600.D0*DEN(5) )*(1/TEMP(2))
        TERM_anomO = (256.D0*DEN(9))*(1/4000.D0)
        TERMnorm1 = 1.D0/(1.D0 + ZL/RE)**2
        TERMnorm2 = ((RE+ZL)/(RE+ALTKM))**2
!
        DRHODZ =TERM1*(TERM_species+TERM_anomO)*TERMnorm1*TERMnorm2
!
!       DRHODZ IS NOW IN G/CC/KM.  THIS IS DIMENSIONALLY EQUAL TO KG/M4.
!
      ENDIF
!------------------------------------------------------------------------
! ORIGINAL CALCULATION:
!      IF(IDRV .NE. 0) THEN
!        TERM1 = -1.66D-24*(16.D0*DEN(1) + 256.D0*DEN(2) + 784.D0*DEN(3) &
!     &          + DEN(7) + 196.D0*DEN(8) )
!        TERM2 = GSURF/(TEMP(2)*RGAS)/(1.D0 + ZL/RE)**2
!        TERM3 = ((RE+ZL)/(RE+ALTKM))**2
!        DRHODZ = TERM1*TERM2*TERM3
!        DRHODZ IS NOW IN G/CC/KM.  THIS IS DIMENSIONALLY EQUAL TO KG/M4.
!
``` -->

In [1]:
import pandas as pd
import numpy as np

import sys  
sys.path.insert(0, '/data/geodyn_proj/analysis/util_funcs/py_read_geodyn_output/')
from a_ReadGEODYN import Read_GEODYN_func_MultipleArcs

%load_ext autoreload
%autoreload 2

##################################
# INPUT PARAMETERS:
##################################

arc_list = ['030914_2wk',
            '030928_2wk',
            '031012_2wk',
#             '031026_2wk',
            '031109_2wk',
            '031123_2wk',
            '031207_2wk',
#             '031221_2wk',
           ]

geodyn_run_params = {}
geodyn_run_params['arc_list']        = arc_list
geodyn_run_params['sat_file']        = 'st'
geodyn_run_params['SAT_ID']          = 7501001
geodyn_run_params['grav_id']         = 'goco05s' 
geodyn_run_params['local_path']      = '/data/geodyn_proj/analysis/starlette_analysis/'
geodyn_run_params['AccelStatus']     = 'acceloff'
geodyn_run_params['den_model']       = 'msis00'
geodyn_run_params['path_to_data']    = ('/data/data_geodyn/results/'+
                                             geodyn_run_params['sat_file']  +'/'+
                                             geodyn_run_params['den_model'] +'/'+  
                                             geodyn_run_params['den_model'] +'_'+ 
                                             geodyn_run_params['AccelStatus']   +'/')
geodyn_run_params['YR']              = 2003
geodyn_run_params['DATA_TYPE']       = 'SLR'
geodyn_run_params['verbose_loading'] = False
geodyn_run_params['Verbose_Stats']   = False

In [2]:
m_edit_drhodz = geodyn_run_params
m_edit_drhodz['den_model']       = 'msis00'
m_edit_drhodz['path_to_data']    = ('/data/data_geodyn/results/'+
                                     m_edit_drhodz['sat_file'] +'/'+
                                     m_edit_drhodz['den_model']+'/'+  
                                     m_edit_drhodz['den_model']+'_'+ 
                                     m_edit_drhodz['AccelStatus'] +'/')
(AdjustedParams_edit,
Trajectory_edit,
Density_edit,
Resids_observed_edit,
Resids_station_summary_edit,
Resids_measure_summary_edit,
RunStats_edit)  = Read_GEODYN_func_MultipleArcs(m_edit_drhodz)   

              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff/st030914_2wk.goco05s

 
Adjusted_params:  19.044567584991455
traj_xyz:  0.023608684539794922
Density file end:  3.6388728618621826
Observed residuals:  1.0269958972930908
residual by station:  3.719740390777588
resid meas summary:  4.97919225692749
save stats to dict:  1.6815264225006104
              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff/st030928_2wk.goco05s

 
Adjusted_params:  18.857430934906006
traj_xyz:  0.06629443168640137
Density file end:  3.6000378131866455
Observed residuals:  1.05125093460083
residual by station:  4.381901025772095
resid meas summary:  5.861712455749512
save stats to dict:  1.6536004543304443
              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff/st031012_2wk.goco05s

 
Adjusted_params:  23.52113938331604
traj_xyz:  0.061318397521972656
Density file end:  3.6687216758728027
Observed residuals:  1.0621535778045654
residual by station:  3.76540470

In [3]:
m_orig_drhodz = geodyn_run_params
m_orig_drhodz['den_model']       = 'msis00_orig_drhodz'
m_orig_drhodz['path_to_data']    = ('/data/data_geodyn/results/'+
                                     m_orig_drhodz['sat_file'] +'/'+
                                     'msis00' +'/'+  
                                     'msis00_acceloff_drhodzOrig'+'/')

(AdjustedParams_orig,
Trajectory_orig,
Density_orig,
Resids_observed_orig,
Resids_station_summary_orig,
Resids_measure_summary_orig,
RunStats_orig)  = Read_GEODYN_func_MultipleArcs(m_orig_drhodz)   

              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff_drhodzOrig/st030914_2wk.goco05s

 
Adjusted_params:  19.440346479415894
traj_xyz:  0.06039905548095703
Density file end:  3.665395736694336
Observed residuals:  1.088761806488037
residual by station:  3.7578463554382324
resid meas summary:  4.957703590393066
save stats to dict:  1.6266541481018066
              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff_drhodzOrig/st030928_2wk.goco05s

 
Adjusted_params:  18.75217318534851
traj_xyz:  0.05665731430053711
Density file end:  3.6382765769958496
Observed residuals:  1.0317761898040771
residual by station:  4.4194724559783936
resid meas summary:  5.863569498062134
save stats to dict:  1.6693110466003418
              Loading /data/data_geodyn/results/st/msis00/msis00_acceloff_drhodzOrig/st031012_2wk.goco05s

 
Adjusted_params:  18.786815404891968
traj_xyz:  0.057501792907714844
Density file end:  3.686589002609253
Observed residuals:  1.053072452545166

In [4]:
name_m1 = 'm00_orig'
name_m2 = 'm00_edit'

In [5]:
import plotly.graph_objects as go
import numpy as np
from plotly.offline import plot, iplot
# %matplotlib inline
from plotly.subplots import make_subplots
import plotly.express as px
# import plotly
# plotly.offline.init_notebook_mode(connected=True)
    
col1 = px.colors.qualitative.Plotly[0]
col2 = px.colors.qualitative.Plotly[1]
col3 = px.colors.qualitative.Plotly[2]

data_nums_1 = 1000
data_nums_2 = 100

fig = make_subplots(rows=2, cols=1, 
    subplot_titles=("Direct Comparison","Percent Difference in Original and Edited DRHODZ"),
                   )

for arcs in arc_list:
    fig.add_trace(go.Scatter(x=Density_orig[arcs]['Date'][::data_nums_2],
                                     y=np.abs(Density_orig[arcs]['drhodz (kg/m**3/m)'][::data_nums_2]),
                                        name=name_m1,
                                         mode='markers',
                                        marker=dict(color=col1,
                                        size=4,
                                        ),
                                       ),
                                        row=1, col=1,
                                       )


    fig.add_trace(go.Scatter(x=Density_edit[arcs]['Date'][::data_nums_2],
                             y=np.abs(Density_edit[arcs]['drhodz (kg/m**3/m)'][::data_nums_2]),
                             name= name_m2,
                             mode='markers',
                             marker=dict(color = col2,
                             size=2,),
                             ),
                            row=1, col=1,
                             )


    A = Density_orig[arcs]['drhodz (kg/m**3/m)'][::data_nums_2]
    B = Density_edit[arcs]['drhodz (kg/m**3/m)'][::data_nums_2]

    C = ((B-A)/A)*100

    fig.add_trace(go.Scatter(x=Density_orig[arcs]['Date'][::data_nums_2],
    #                          y=C**(np.log10(C)),
                             y=C,
                             name = '% diff',
                             mode='markers',
                                marker=dict(color='green',
                                size=3,
                                ),
    #                           showlegend=False,

                               ),
                               row=2, col=1,
                               )




fig.update_layout(
    title="Modifying DRHODZ-- Comparison",
    )
fig.update_yaxes(type="log", exponentformat= 'power', row=1, col=1)
# fig.update_yaxes( exponentformat= 'power', row=2 , col=1)

fig.update_yaxes(   exponentformat= 'power',)
fig.update_layout(legend= {'itemsizing': 'constant'})

fig.update_yaxes(title_text="kg/m^4", row=1, col=1)
fig.update_yaxes(title_text="%", row=2, col=1)

fig.update_xaxes(title_text="Date", row=1, col=1)
fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_layout(legend= {'itemsizing': 'constant'})
#     fig.update_xaxes(tickangle=45)
fig.update_layout(
    autosize=False,
    width=900,
    height=700,
)
fig.update_layout(
    font=dict(
#             family="Courier New, monospace",
        size=14,
             ),)


iplot(fig)


In [6]:
# import os

# # if not os.path.exists("msis_update_images"):
# #     os.mkdir("msis_update_images")

# fig.write_image("plot_drhodz_msis00_eval.png")
